In [1]:
import json
import pandas as pd
import numpy as np

In [2]:
a= open ('dump.json', "r")
data=json.load(a)
df = pd.read_json("dump.json")

In [3]:
df_trmidhi = df.loc[df['book_id']==7895]

In [4]:
pd.set_option('display.max_rows',7000)
pd.set_option('display.max_colwidth',None)
df_trial = df_trmidhi.loc[:,"clean_texts"]

In [5]:
def is_numb(word):
    for w in word:
        if w  in ar_num:
            isit = True
        else:
            isit = False
            break
    return isit


        
def translate(num):
    try:
        eng_equi=''
        for i in range(0,len(num)):
                temp = ar_num.index(num[i])
                eng_equi += eng_num[temp]
    except:
        temp = 0
    return eng_equi

    
hadith = []  
index = []
hadith_number = []
ar_num = ['٨','٦','٩','٥','٣','٧','٢','٤','١',' ','-','(', ')','م', '٠','ب']
eng_num = ['8', '6', '9', '5', '3', '7', '2', '4','1', ' ', '-', '(', ')', 'M','0','B']
count = 0
for i in df_trial:
    j = " ".join(i)
    w = j.split()
    if not (w[0].startswith('~') or w[0].startswith('(')):
        hadith.append(j)
        index.append(df_trial.index[count])
        if(is_numb(w[0])):
            hadith_number.append(translate(w[0]))
        else:
            hadith_number.append(0)
    #else:
    #    if(is_numb(w[0]) and len(w)>2):
    #        if (((w[1] and w[2]) != "بَابُ") or ((w[1] and w[2]) != "باب") or ((w[1] and w[2])  !="بَابُ:") or ((w[1] and w[2]) != "باب:")):
    #            hadith.append(j)
    #            index.append(df_trial.index[count])
    #            hadith_number.append(translate(w[0]))
    #        
    #    
    count+=1


In [9]:
new_df = pd.DataFrame(hadith,index = index,columns=['clean_texts'])
hadith_number = pd.DataFrame(hadith_number, columns = ['hadith_number'])

In [10]:
new_df.drop(columns=['clean_texts'], inplace = True)
new_df = new_df.join(df_trmidhi,how='left')
new_df = new_df.reset_index()

In [11]:
#pd.set_option('display.max_rows',4500)
new_df = pd.concat([new_df, hadith_number],axis=1)

In [13]:
anomaly_df = new_df.loc[new_df['hadith_number']==0]

In [14]:
new_df.drop(anomaly_df.index,inplace=True)

In [15]:
len(new_df)

4323

In [18]:
keep = [3,6,8,9,20,22,24,27,29,32,46,49,57,58,61,63,64,67,68]
anomaly_df = anomaly_df.iloc[keep]

In [19]:
len(anomaly_df)

19

In [20]:
clean_anomaly = anomaly_df.loc[:,'clean_texts']

hadith_anomaly = []
number_anomaly = []
index_anomaly  = []

def cut(hadith):
    h = " ".join(hadith)
    w = h.split()
    for i in range(len(w)):
        if is_numb(w[i]):
            had = " ".join(w[i:])
            numb = w[i]
            break
        
            
    return had, numb


for i in range (len(clean_anomaly)):
    print(i)
    if i == 18:
        hadith_anomaly.append(clean_anomaly.iloc[0][1])
        hadith_anomaly.append(clean_anomaly.iloc[0][2])
        number_anomaly.append(translate(clean_anomaly.iloc[0][1][0:3]))
        number_anomaly.append(translate(clean_anomaly.iloc[0][2][0:3]))
        index_anomaly.append(clean_anomaly.index[i])
        index_anomaly.append(clean_anomaly.index[i])

    elif (i != 1 and i !=4 and i !=13 and i !=17):
        new_hadith, new_numb = cut(clean_anomaly.iloc[i])
        hadith_anomaly.append(new_hadith)
        number_anomaly.append(translate(new_numb))
        index_anomaly.append(clean_anomaly.index[i])
    else:
        hadith_anomaly.append(clean_anomaly.iloc[i])
        number_anomaly.append(0)
        index_anomaly.append(clean_anomaly.index[i])
        

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18


In [21]:
newer_df = pd.DataFrame(hadith_anomaly,index = index_anomaly,columns=['clean_texts'])
hadith_anomaly_number = pd.DataFrame(number_anomaly,index = index_anomaly ,columns = ['hadith_number'])

In [22]:
anomaly_df=anomaly_df.drop(columns='clean_texts')
newer_df = newer_df.join(anomaly_df,how='inner')


In [23]:
#newer_df = newer_df.reset_index()
newer_df.drop(columns='hadith_number', inplace=True)
newer_df = newer_df.join(hadith_anomaly_number,how='left')



In [25]:
newer_df = new_df.append(newer_df)

In [30]:
newer_df.loc[:,['clean_texts', 'page_id','hadith_number']].sort_values(by ='page_id').tail(1000)

clean_texts  \
2635                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

In [28]:
newer_df.to_json("Final_tirmdhi",orient='records',force_ascii = False)

In [31]:
len(newer_df)

4345